# Assignment 4 - Text Analysis
An explanation this assignment could be found in the .pdf explanation document


## Materials to review for this assignment
<h4>From Moodle:</h4> 
<h5><u>Review the notebooks regarding the following python topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Working with strings</b> (tutorial 8 notebook)<br/>
&#x2714; <b>Text Analysis</b> (tutorial 9 notebook)<br/>
&#x2714; <b>Hebrew text analysis tools (tokenizer, wordnet)</b> (moodle example)<br/>
&#x2714; <b>(brief review) All previous notebooks</b><br/>
</div> 
<h5><u>Review the presentations regarding the following topics</u>:</h5>
<div class="alert alert-info">
&#x2714; <b>Text Analysis</b> (lecture 9 presentation)<br/>
&#x2714; <b>(brief review) All other presentations</b><br/>
</div>

## Preceding Step - import modules (packages)
This step is necessary in order to use external modules (packages). <br/>

In [1]:
# --------------------------------------
import pandas as pd
import numpy as np
# --------------------------------------


# --------------------------------------
# ------------- visualizations:
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib.colors import ListedColormap
# --------------------------------------


# ---------------------------------------
import sklearn
from sklearn import preprocessing, metrics, pipeline, model_selection, feature_extraction 
from sklearn import naive_bayes, linear_model, svm, neural_network, neighbors, tree
from sklearn import decomposition, cluster

from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV 
from sklearn.pipeline import Pipeline
from sklearn.metrics import accuracy_score, confusion_matrix
from sklearn.metrics import precision_score, recall_score, f1_score
from sklearn.metrics import mean_squared_error, r2_score, silhouette_score
from sklearn.preprocessing import MinMaxScaler, StandardScaler, LabelEncoder

from sklearn.svm import LinearSVC
from sklearn.neural_network import MLPClassifier
from sklearn.linear_model import Perceptron, SGDClassifier
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.naive_bayes import MultinomialNB, GaussianNB
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
# ---------------------------------------


# ----------------- output and visualizations: 
import warnings
from sklearn.exceptions import ConvergenceWarning
warnings.simplefilter("ignore")
warnings.simplefilter(action='ignore', category=FutureWarning)
warnings.simplefilter("ignore", category=ConvergenceWarning)
# show several prints in one cell. This will allow us to condence every trick in one cell.
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = "all"
%matplotlib inline
pd.pandas.set_option('display.max_columns', None)
pd.set_option('display.float_format', lambda x: '%.3f' % x)
# ---------------------------------------

### Text analysis and String manipulation imports:

In [2]:
# --------------------------------------
# --------- Text analysis and Hebrew text analysis imports:
# vectorizers:
from sklearn.feature_extraction import text
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer

# regular expressions:
import re
# --------------------------------------

### (optional) Hebrew text analysis - WordNet (for Hebrew)
Note: the WordNet is not a must

#### (optional) Only if you didn't install Wordnet (for Hebrew) use:

In [3]:
!pip install wn
!python -m wn download omw-he:1.4


Cached file found: C:\Users\Nati\.wn_data\downloads\7ecf10e89326bc0ac26ad94b40fe60a7b6ac3302

Checking C:\Users\Nati\AppData\Local\Temp\tmplzaoq0sg\omw-he\omw-he.xml
Skipping omw-he:1.4 (Hebrew Wordnet); already added



In [4]:
# word net
import wn

### (optional) Hebrew text analysis - hebrew_tokenizer (Tokenizer for Hebrew)
Note: the hebrew_tokenizer is not a must

#### (optional) Only if you didn't install hebrew_tokenizer use:

In [5]:
!pip install hebrew_tokenizer

In [6]:
# tokenizer:
import hebrew_tokenizer as ht

C:\Users\Nati\Downloads\למידת מכונה\Ex4


### Reading input files
Reading input files for train annotated corpus (raw text data) corpus and for the test corpus

In [7]:
train_filename = 'annotated_corpus_for_train.csv'
test_filename  = 'corpus_for_test.csv'
df_train = pd.read_csv(train_filename, index_col=None, encoding='utf-8')
df_test  = pd.read_csv(test_filename, index_col=None, encoding='utf-8')

In [8]:
df_train.head(8)
df_train.shape
df_test.head()

story gender
0  כשחבר הזמין אותי לחול, לא באמת חשבתי שזה יקרה,...      m
1  לפני שהתגייסתי לצבא עשיתי כל מני מיונים ליחידו...      m
2  מאז שהתחילו הלימודים חלומו של כל סטודנט זה הפנ...      f
3  כשהייתי ילד, מטוסים היה הדבר שהכי ריתק אותי. ב...      m
4  ‏הייתי מדריכה בכפר נוער ומתאם הכפר היינו צריכי...      f
5  לפני כ3 חודשים טסתי לרומא למשך שבוע. טסתי במטו...      f
6  אני כבר שנתיים נשוי והשנה אני ואישתי סוף סוף י...      m
7  השנה התחלנו שיפוץ בדירה שלנו בתל אביב. הדירה ה...      f

(753, 2)

test_example_id                                              story
0                0  כל קיץ אני והמשפחה נוסעים לארצות הברית לוס אנג...
1                1  הגעתי לשירות המדינה אחרי שנתיים כפעיל בתנועת "...
2                2  אחת האהבות הגדולות שלי אלו הכלבים שלי ושל אישת...
3                3  רגע הגיוס לצבא היה הרגע הכי משמעותי עבורי, אני...
4                4  אני הגעתי לברזיל ישר מקולומביה וגם אני עשיתי ע...

In [9]:
df_test.head(3)

test_example_id                                              story
0                0  כל קיץ אני והמשפחה נוסעים לארצות הברית לוס אנג...
1                1  הגעתי לשירות המדינה אחרי שנתיים כפעיל בתנועת "...
2                2  אחת האהבות הגדולות שלי אלו הכלבים שלי ושל אישת...

### Your implementation:
Write your code solution in the following code-cells

In [10]:
# Name: Natanel Mosheashvili ; # ID: 205636731

In [11]:
Tf_Vector = TfidfVectorizer(ngram_range=(2,3), max_features = 18000, max_df=0.9, min_df=2,sublinear_tf=True)
Tf_transform = Tf_Vector.fit_transform(df_train['story']) 
new_df = pd.DataFrame(Tf_transform.toarray())
new_df

0      1      2      3      4      5      6      7      8      9      \
0    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
3    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
4    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
748  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
749  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
750  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
751  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
752  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   

     10     11     12     13     14     15     16     17     18     19     \
0    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2    0.000  0.000  0.000  0.000  0.000  0.099  0.000  0.000  0.000  0.000   
3    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
4    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
748  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
749  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
750  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
751  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
752  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   

     20     21     22     23     24     25     26     27     28     29     \
0    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
3    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
4    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
748  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
749  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
750  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
751  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
752  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   

     30     31     32     33     34     35     36     37     38     39     \
0    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
3    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
4    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
..     ...    ...    ...    ...    ...    ...    ...    ...    ...    ...   
748  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
749  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
750  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
751  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
752  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   

     40     41     42     43     44     45     46     47     48     49     \
0    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
1    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000   
2    0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000  0.000 

In [28]:
X_train, X_test, y_train, y_test = train_test_split(new_df, df_train['gender'], test_size=0.25, random_state=42)

#file was to big to upload to the mud

#print('# - X_train: ')
#X_train
#print('# - y_train: ')
#y_train
#print('# - X_test: ')
#X_test
#print('# - y_test: ')
#y_test

In [29]:
fClass = KNeighborsClassifier(n_neighbors = 1)

fClass.fit(X_train, y_train == "f")

mClass = KNeighborsClassifier(n_neighbors = 1)

mClass.fit(X_train, y_train == "m")

KNeighborsClassifier(n_neighbors=1)

KNeighborsClassifier(n_neighbors=1)

In [30]:
female_Test_pred = fClass.predict(X_test)

female_Train_pred = fClass.predict(X_train)

male_Test_pred = mClass.predict(X_test)

male_Train_pred = mClass.predict(X_train)

In [31]:
female_Train_score = f1_score(y_train == "f", female_Train_pred, average='macro')
male_Train_score = f1_score(y_train == "m" , male_Train_pred, average='macro')

Train_score = (male_Train_score + female_Train_score) /2
print(Train_score)

1.0


In [32]:
female_Test_score = f1_score(y_test == "f", female_Test_pred, average='macro')
male_Test_score = f1_score(y_test == "m", male_Test_pred, average='macro')

Test_score = (male_Test_score + female_Test_score) /2
print(Test_score)

0.7237824386775684


In [33]:
VectorFit = Tf_Vector.fit_transform(pd.concat([df_train['story'], df_test['story']]))

VectorDf = pd.DataFrame(VectorFit.toarray())

male_cls = KNeighborsClassifier(n_neighbors = 1)

male_cls.fit(VectorDf[:753], df_train['gender'] == "m")

Pred_y = male_cls.predict(VectorDf[753:])

Df_pred = pd.DataFrame({'test_example_id':df_test['test_example_id'],'predicted_category':Pred_y})

Df_pred.replace({'predicted_category':{True:'m',False:'f'}},inplace = True)

pd.set_option('max_rows',323)

Df_pred

KNeighborsClassifier(n_neighbors=1)

test_example_id predicted_category
0                  0                  m
1                  1                  m
2                  2                  m
3                  3                  m
4                  4                  m
5                  5                  m
6                  6                  m
7                  7                  m
8                  8                  m
9                  9                  m
10                10                  m
11                11                  m
12                12                  f
13                13                  m
14                14                  m
15                15                  m
16                16                  m
17                17                  m
18                18                  m
19                19                  m
20                20                  m
21                21                  f
22                22                  m
23                23                  m
24                24                  m
25                25                  m
26                26                  m
27                27                  m
28                28                  f
29                29                  m
30                30                  m
31                31                  m
32                32                  m
33                33                  m
34                34                  m
35                35                  m
36                36                  m
37                37                  m
38                38                  f
39                39                  m
40                40                  m
41                41                  m
42                42                  m
43                43                  m
44                44                  m
45                45                  f
46                46                  m
47                47                  m
48                48                  m
49                49                  m
50                50                  f
51                51                  m
52                52                  m
53                53                  m
54                54                  m
55                55                  m
56                56                  m
57                57                  m
58                58                  m
59                59                  m
60                60                  m
61                61                  f
62                62                  f
63                63                  m
64                64                  f
65                65                  m
66                66                  m
67                67                  f
68                68                  m
69                69                  m
70                70                  m
71                71                  m
72                72                  m
73                73                  f
74                74                  f
75                75                  f
76                76                  f
77                77                  m
78                78                  m
79                79                  m
80                80                  m
81                81                  m
82                82                  m
83                83                  f
84                84                  m
85                85                  m
86                86                  m
87                87                  f
88                88                  f
89                89                  m
90                90                  m
91                91                  m
92                92                  m
93                93                  m
94                94                  f
95                95                  m
96                96                  f
97                97                  m
98                98                  m
99   

### Save output to csv
After you're done save your output to the 'classification_results.csv' csv file.<br/>
We assume that the dataframe with your results contain the following columns:
* column 1 (left column): 'test_example_id'  - the same id associated to each of the test stories to be predicted.
* column 2 (right column): 'predicted_category' - the predicted gender value for each of the associated story. 

Assuming your predicted values are in the `df_predicted` dataframe, you should save you're results as following:

In [34]:
Df_pred.to_csv('classification_results.csv',index=False)